pip install torch transformers sklearn pandas

For Mac M1:

curl --proto '=https' --tlsv1.2 -sSf https://sh.rustup.rs | sh

In [ ]:
from transformers import pipeline, set_seed
generator = pipeline('text-generation', model='gpt2')
set_seed(42)
generator("Hello, I'm Elon Musk,", max_length=30, num_return_sequences=5)

In [29]:
import pandas as pd
from sklearn.model_selection import train_test_split

data = pd.read_csv("dataset/train_cleaned.csv")['content'].to_numpy()
train, test = train_test_split(data,test_size=0.15)
traindata = ''
testdata = ''
for i in train:
    traindata += i.replace("&amp", "") +'\n'
f = open('train_dataset.txt','w')
f.write(traindata)
for i in test:
    testdata += i.replace("&amp","") +'\n'
f = open('test_dataset.txt','w')
f.write(testdata)

171335

In [30]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("gpt2")
if tokenizer.pad_token is None:
    tokenizer.add_special_tokens({'pad_token': '[PAD]'})
train_path = 'train_dataset.txt'
test_path = 'test_dataset.txt'

Could not locate the tokenizer configuration file, will try to use the model config instead.
loading configuration file https://huggingface.co/gpt2/resolve/main/config.json from cache at /Users/yu/.cache/huggingface/transformers/fc674cd6907b4c9e933cb42d67662436b89fa9540a1f40d7c919d0109289ad01.7d2e0efa5ca20cef4fb199382111e9d3ad96fd77b849e1d4bed13a66e1336f51
Model config GPT2Config {
  "_name_or_path": "gpt2",
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "initializer_range": 0.02,
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 12,
  "n_positions": 1024,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_label

In [38]:
from transformers import LineByLineTextDataset
from transformers import Trainer, TrainingArguments, AutoModelWithLMHead

model = AutoModelWithLMHead.from_pretrained("gpt2")
dataset = LineByLineTextDataset(
    tokenizer=tokenizer,
    file_path=train_path,
    block_size=1,
)

from transformers import DataCollatorForLanguageModeling
data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer, mlm=False
)

from transformers import Trainer, TrainingArguments
training_args = TrainingArguments(
    output_dir="./gpt2-musk",
    overwrite_output_dir=True,
    num_train_epochs=1,
    per_gpu_train_batch_size=1,
    save_steps=100,
    save_total_limit=2,
)

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=dataset,
    #prediction_loss_only=True,
)

loading configuration file https://huggingface.co/gpt2/resolve/main/config.json from cache at /Users/yu/.cache/huggingface/transformers/fc674cd6907b4c9e933cb42d67662436b89fa9540a1f40d7c919d0109289ad01.7d2e0efa5ca20cef4fb199382111e9d3ad96fd77b849e1d4bed13a66e1336f51
Model config GPT2Config {
  "_name_or_path": "gpt2",
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "initializer_range": 0.02,
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 12,
  "n_positions": 1024,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params"

In [25]:
from transformers import TextDataset,DataCollatorForLanguageModeling

def load_dataset(train_path,test_path,tokenizer):
    train_dataset = TextDataset(
          tokenizer=tokenizer,
          file_path=train_path,
          block_size=128)

    test_dataset = TextDataset(
          tokenizer=tokenizer,
          file_path=test_path,
          block_size=128)

    data_collator = DataCollatorForLanguageModeling(
        tokenizer=tokenizer, mlm=False,
    )
    return train_dataset,test_dataset,data_collator

train_dataset,test_dataset,data_collator = load_dataset(train_path,test_path,tokenizer)


/opt/anaconda3/envs/DL/lib/python3.9/site-packages/transformers/data/datasets/language_modeling.py:54: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(
Loading features from cached file cached_lm_GPT2TokenizerFast_128_train_dataset.txt [took 0.031 s]
Loading features from cached file cached_lm_GPT2TokenizerFast_128_test_dataset.txt [took 0.002 s]


In [7]:
for id, tensor  in enumerate(train_dataset):
    print(tensor)

tensor([22797,    88,  1869, 29234, 25239,  1262,   262,  1176,   286, 21296,
          198,    68,    61,  1343,   796,   198,    39, 12236,  7427,   198,
           51, 14992,   284,   900,   257,   922,  1672,   198, 17320, 15537,
         3781,    13, 29051,   257,  1178, 19225,    14, 32683,     5, 13655,
           26,     5, 13655,    26,    16,   661,   287,   534,  2912,  4704,
        42254,    13, 16126, 45951, 24876,  4249, 27699,    11,   543,   389,
         3729,   922,  2706,    11,   714,  1826,   597,   286,   674, 12971,
           11,  7269,    11,  1575,   393,  1176,  5359,    13,   198, 34784,
         2795,   198,  2061,   339, 46701,  1656,   284,  9144,   318,   326,
         1230,   318,   655,   257, 30797,   396, 12017,   287,   262,  4179,
          198,    54,   756,   307,  1909,    11, 11481,  9439,   198, 20418,
          527, 28930,   654,   286,  8706,   198,   464, 26920,   615, 19397,
        13619,   318, 13526,   198, 22743,   278,   428,   318])

In [11]:
from transformers import LineByLineTextDataset,DataCollatorForLanguageModeling

def load_dataset(train_path,test_path,tokenizer):
    train_dataset = LineByLineTextDataset(
          tokenizer=tokenizer,
          file_path=train_path,
          block_size=128)

    test_dataset = LineByLineTextDataset(
          tokenizer=tokenizer,
          file_path=test_path,
          block_size=128)

    data_collator = DataCollatorForLanguageModeling(
          tokenizer=tokenizer, mlm=False, mlm_probability=0.15
          )
    
    return train_dataset,test_dataset,data_collator

train_dataset,test_dataset,data_collator = load_dataset(train_path,test_path,tokenizer)

Creating features from dataset file at train_dataset.txt
Creating features from dataset file at test_dataset.txt


In [7]:
type(train_dataset)

transformers.data.datasets.language_modeling.LineByLineTextDataset

In [8]:
for idx, tensor  in enumerate(train_dataset):
    print(tensor)

{'input_ids': tensor([22797,    88,  1869, 29234, 25239,  1262,   262,  1176,   286, 21296])}
{'input_ids': tensor([  68,   61, 1343,  796])}
{'input_ids': tensor([   39, 12236,  7427])}
{'input_ids': tensor([   51, 14992,   284,   900,   257,   922,  1672])}
{'input_ids': tensor([17320, 15537,  3781,    13, 29051,   257,  1178, 19225,    14, 32683,
            5, 13655,    26,     5, 13655,    26,    16,   661,   287,   534,
         2912,  4704, 42254,    13, 16126, 45951, 24876,  4249, 27699,    11,
          543,   389,  3729,   922,  2706,    11,   714,  1826,   597,   286,
          674, 12971,    11,  7269,    11,  1575,   393,  1176,  5359,    13])}
{'input_ids': tensor([34784,  2795])}
{'input_ids': tensor([ 2061,   339, 46701,  1656,   284,  9144,   318,   326,  1230,   318,
          655,   257, 30797,   396, 12017,   287,   262,  4179])}
{'input_ids': tensor([   54,   756,   307,  1909,    11, 11481,  9439])}
{'input_ids': tensor([20418,   527, 28930,   654,   286,  8706])}

In [21]:
from transformers import Trainer, TrainingArguments, AutoModelWithLMHead

model = AutoModelWithLMHead.from_pretrained("gpt2")

training_args = TrainingArguments(
    output_dir="./gpt2-musk", #The output directory
    overwrite_output_dir=True, #overwrite the content of the output directory
    num_train_epochs=3, # number of training epochs
    per_device_train_batch_size=32, # batch size for training
    per_device_eval_batch_size=64,  # batch size for evaluation
    eval_steps = 40, # Number of update steps between two evaluations.
    save_steps=80, # after # steps model is saved
    warmup_steps=50,# number of warmup steps for learning rate scheduler
    )

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
    #eval_dataset=test_dataset,
    #prediction_loss_only=True,
)

loading configuration file https://huggingface.co/gpt2/resolve/main/config.json from cache at /Users/yu/.cache/huggingface/transformers/fc674cd6907b4c9e933cb42d67662436b89fa9540a1f40d7c919d0109289ad01.7d2e0efa5ca20cef4fb199382111e9d3ad96fd77b849e1d4bed13a66e1336f51
Model config GPT2Config {
  "_name_or_path": "gpt2",
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "initializer_range": 0.02,
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 12,
  "n_positions": 1024,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params"

In [39]:
trainer.train()

Using deprecated `--per_gpu_train_batch_size` argument which will be removed in a future version. Using `--per_device_train_batch_size` is preferred.
***** Running training *****
  Num examples = 14262
  Num Epochs = 1
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 1
  Gradient Accumulation steps = 1
  Total optimization steps = 14262


KeyboardInterrupt: 

In [ ]:
trainer.save_model()

In [ ]:
from transformers import pipeline

tweet = pipeline('text-generation',model='gpt2-musk', tokenizer=tokenizer )

In [ ]:
#generator = pipeline('text-generation', model='gpt2')
from transformers import pipeline, set_seed
set_seed(42)
tweet("With steel membrane wings like a Dragon,", max_length=50, num_return_sequences=5)